<a href="https://colab.research.google.com/github/darshbaxi/axios_week_project/blob/main/sentiment_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [123]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import tensorflow as tf
import keras

## Reading Dataset

In [124]:
df=pd.read_csv('IMDB Dataset.csv',engine='python')

In [125]:
df

review sentiment
0      One of the other reviewers has mentioned that ...  positive
1      A wonderful little production. <br /><br />The...  positive
2      I thought this was a wonderful way to spend ti...  positive
3      Basically there's a family where a little boy ...  negative
4      Petter Mattei's "Love in the Time of Money" is...  positive
...                                                  ...       ...
49995  I thought this movie did a down right good job...  positive
49996  Bad plot, bad dialogue, bad acting, idiotic di...  negative
49997  I am a Catholic taught in parochial elementary...  negative
49998  I'm going to have to disagree with the previou...  negative
49999  No one expects the Star Trek movies to be high...  negative

[50000 rows x 2 columns]

In [126]:
x=df['review']

In [127]:
y=df['sentiment']

In [128]:
x.shape

(50000,)

In [129]:
y.shape

(50000,)

In [130]:
y=list(map(lambda i:0 if i=='negative' else 1,y ))

In [131]:
y[:10]

[1, 1, 1, 0, 1, 1, 1, 0, 0, 1]

In [132]:
x[:2]

0    One of the other reviewers has mentioned that ...
1    A wonderful little production. <br /><br />The...
Name: review, dtype: object

## Data Cleaning

In [133]:
import re
removal_tag=re.compile("<[a-zA-Z]+\s\/>")

In [134]:
def tagremove(text):
  return removal_tag.sub(' ',text)

In [135]:
x_tag_removal=[]
for i in range(len(x)):
  sent=x[i]
  x_tag_removal.append(tagremove(sent))




In [136]:
x_tag_removal[:2]

["One of the other reviewers has mentioned that after watching just 1 Oz episode you'll be hooked. They are right, as this is exactly what happened with me.  The first thing that struck me about Oz was its brutality and unflinching scenes of violence, which set in right from the word GO. Trust me, this is not a show for the faint hearted or timid. This show pulls no punches with regards to drugs, sex or violence. Its is hardcore, in the classic use of the word.  It is called OZ as that is the nickname given to the Oswald Maximum Security State Penitentary. It focuses mainly on Emerald City, an experimental section of the prison where all the cells have glass fronts and face inwards, so privacy is not high on the agenda. Em City is home to many..Aryans, Muslims, gangstas, Latinos, Christians, Italians, Irish and more....so scuffles, death stares, dodgy dealings and shady agreements are never far away.  I would say the main appeal of the show is due to the fact that it goes where other s

In [137]:
len(x_tag_removal)

50000

In [138]:
import nltk
from nltk.stem import PorterStemmer as ps
from nltk.stem import WordNetLemmatizer as wl
from nltk.corpus import stopwords
nltk.download('punkt')
nltk.download('stopwords')
lammtizer=wl()
stemmer=ps()
nltk.download('wordnet')


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [139]:
corpus=[]
for i in range(len(x_tag_removal)):
  sentence=re.sub('[^a-zA-Z]',' ',x_tag_removal[i])
  sentence=re.sub('\s+',' ',sentence)
  sentence=sentence.lower()
  word=nltk.word_tokenize(sentence)
  arr=[]
  for j in word:
    if j not in set(stopwords.words('english')):
      arr.append(stemmer.stem(j))
  sentence=' '.join(arr)
  corpus.append(sentence)

In [140]:
corpus


['one review mention watch oz episod hook right exactli happen first thing struck oz brutal unflinch scene violenc set right word go trust show faint heart timid show pull punch regard drug sex violenc hardcor classic use word call oz nicknam given oswald maximum secur state penitentari focus mainli emerald citi experiment section prison cell glass front face inward privaci high agenda em citi home mani aryan muslim gangsta latino christian italian irish scuffl death stare dodgi deal shadi agreement never far away would say main appeal show due fact goe show dare forget pretti pictur paint mainstream audienc forget charm forget romanc oz mess around first episod ever saw struck nasti surreal say readi watch develop tast oz got accustom high level graphic violenc violenc injustic crook guard sold nickel inmat kill order get away well manner middl class inmat turn prison bitch due lack street skill prison experi watch oz may becom comfort uncomfort view that get touch darker side',
 'won

In [141]:
len(corpus)

50000

In [142]:
maxlength=0
for i in range(len(corpus)):
  if(maxlength<len(corpus[i])):
    maxlength=len(corpus[i])

maxlength

8290

## Reading Glove File

In [143]:


file=open('/content/glove.6B.100d.txt','r',encoding='utf8')

In [144]:
file_content=file.readlines()

In [145]:
file_content

['the -0.038194 -0.24487 0.72812 -0.39961 0.083172 0.043953 -0.39141 0.3344 -0.57545 0.087459 0.28787 -0.06731 0.30906 -0.26384 -0.13231 -0.20757 0.33395 -0.33848 -0.31743 -0.48336 0.1464 -0.37304 0.34577 0.052041 0.44946 -0.46971 0.02628 -0.54155 -0.15518 -0.14107 -0.039722 0.28277 0.14393 0.23464 -0.31021 0.086173 0.20397 0.52624 0.17164 -0.082378 -0.71787 -0.41531 0.20335 -0.12763 0.41367 0.55187 0.57908 -0.33477 -0.36559 -0.54857 -0.062892 0.26584 0.30205 0.99775 -0.80481 -3.0243 0.01254 -0.36942 2.2167 0.72201 -0.24978 0.92136 0.034514 0.46745 1.1079 -0.19358 -0.074575 0.23353 -0.052062 -0.22044 0.057162 -0.15806 -0.30798 -0.41625 0.37972 0.15006 -0.53212 -0.2055 -1.2526 0.071624 0.70565 0.49744 -0.42063 0.26148 -1.538 -0.30223 -0.073438 -0.28312 0.37104 -0.25217 0.016215 -0.017099 -0.38984 0.87424 -0.72569 -0.51058 -0.52028 -0.1459 0.8278 0.27062\n',
 ', -0.10767 0.11053 0.59812 -0.54361 0.67396 0.10663 0.038867 0.35481 0.06351 -0.094189 0.15786 -0.81665 0.14172 0.21939 0.58505 -

In [146]:
embedding={}
for i in file_content:
  senc=i.split()
  embedding[senc[0]]=np.array(senc[1:],dtype='float')

In [147]:
len(embedding['the'])

100

## Converting Text into Vector using Tokenizer

In [148]:
from keras.preprocessing.text import Tokenizer
word_total = Tokenizer()
word_total.fit_on_texts(corpus)
wordindex=word_total.word_index
vocab_length = len(wordindex)+1

In [149]:
vocab_length

69014

In [150]:
wordindex

{'movi': 1,
 'film': 2,
 'one': 3,
 'like': 4,
 'time': 5,
 'good': 6,
 'make': 7,
 'charact': 8,
 'see': 9,
 'get': 10,
 'watch': 11,
 'even': 12,
 'stori': 13,
 'would': 14,
 'realli': 15,
 'well': 16,
 'scene': 17,
 'look': 18,
 'show': 19,
 'much': 20,
 'end': 21,
 'bad': 22,
 'great': 23,
 'peopl': 24,
 'go': 25,
 'love': 26,
 'also': 27,
 'first': 28,
 'think': 29,
 'act': 30,
 'play': 31,
 'way': 32,
 'thing': 33,
 'made': 34,
 'could': 35,
 'know': 36,
 'say': 37,
 'seem': 38,
 'work': 39,
 'plot': 40,
 'actor': 41,
 'two': 42,
 'mani': 43,
 'seen': 44,
 'come': 45,
 'year': 46,
 'want': 47,
 'take': 48,
 'never': 49,
 'life': 50,
 'best': 51,
 'tri': 52,
 'littl': 53,
 'ever': 54,
 'man': 55,
 'better': 56,
 'give': 57,
 'still': 58,
 'find': 59,
 'perform': 60,
 'feel': 61,
 'part': 62,
 'use': 63,
 'someth': 64,
 'director': 65,
 'actual': 66,
 'back': 67,
 'lot': 68,
 'interest': 69,
 'real': 70,
 'guy': 71,
 'old': 72,
 'funni': 73,
 'cast': 74,
 'though': 75,
 'live': 76,

In [151]:
Xtokens = word_total.texts_to_sequences(corpus)
Xtokens


[[3,
  237,
  354,
  11,
  2646,
  189,
  1585,
  112,
  557,
  107,
  28,
  33,
  2757,
  2646,
  1093,
  10869,
  17,
  495,
  86,
  112,
  289,
  25,
  1344,
  19,
  4817,
  333,
  8118,
  19,
  583,
  1645,
  1058,
  600,
  313,
  495,
  3175,
  236,
  63,
  289,
  153,
  2646,
  6225,
  305,
  10686,
  5329,
  1808,
  502,
  33796,
  1114,
  1288,
  15530,
  427,
  3275,
  1881,
  756,
  1869,
  1764,
  854,
  204,
  16008,
  11896,
  225,
  3619,
  2504,
  427,
  269,
  43,
  10005,
  3373,
  9045,
  5519,
  1044,
  896,
  2141,
  14261,
  229,
  2036,
  5643,
  407,
  6623,
  6310,
  49,
  146,
  165,
  14,
  37,
  202,
  792,
  19,
  606,
  102,
  195,
  19,
  1495,
  663,
  103,
  273,
  1017,
  2193,
  178,
  663,
  617,
  663,
  736,
  2646,
  709,
  108,
  28,
  189,
  54,
  129,
  2757,
  1385,
  1726,
  37,
  1428,
  11,
  364,
  918,
  2646,
  105,
  7546,
  225,
  445,
  1191,
  495,
  495,
  5042,
  2881,
  1695,
  2570,
  14647,
  4288,
  100,
  459,
  10,
  165,
  16

In [155]:
x_train=tf.keras.utils.pad_sequences(Xtokens,maxlen=25,padding='post')

In [156]:
x_train

array([[  970,   570,   558, ...,   438,  3374,   360],
       [ 1146,   497,  1581, ...,   270,    16,   138],
       [  367,   968,  1126, ...,    25,     9,   119],
       ...,
       [  704,    76,  3865, ...,  3223, 15604,  1044],
       [ 1657,     3,     3, ...,  1795,  1417,   325],
       [ 5021, 22111,    14, ...,   907,   564,     1]], dtype=int32)

In [157]:
x_train.shape

(50000, 25)

In [ ]:
wordindex.items()

## Building Embedding Matrix

In [158]:
embed_size = 100
embeddingmatrix = np.zeros((vocab_length, embed_size))
for word, i in wordindex.items():
    embed_vector = embedding.get(word)
    if embed_vector is not None:
       embeddingmatrix[i] = embed_vector




In [159]:
embeddingmatrix.shape

(69014, 100)

In [160]:
embeddingmatrix

array([[ 0.      ,  0.      ,  0.      , ...,  0.      ,  0.      ,
         0.      ],
       [ 0.      ,  0.      ,  0.      , ...,  0.      ,  0.      ,
         0.      ],
       [ 0.19916 , -0.049702,  0.24579 , ..., -0.068109,  0.017651,
         0.06455 ],
       ...,
       [ 0.      ,  0.      ,  0.      , ...,  0.      ,  0.      ,
         0.      ],
       [ 0.      ,  0.      ,  0.      , ...,  0.      ,  0.      ,
         0.      ],
       [ 0.027842,  0.59833 ,  0.53633 , ...,  0.12272 ,  0.48018 ,
         0.54391 ]])

## Building  Model

In [161]:
from keras.layers import LSTM,Dense,Embedding,Bidirectional
from keras.models import Sequential

In [162]:
model = Sequential([
    Embedding(input_dim = len(wordindex) + 1,
              output_dim = embed_size,
              input_length = 25,
              weights = [embeddingmatrix],
              trainable=False
             ),
    LSTM(64,return_sequences=True),
    LSTM(16),
    Dense(1, activation = 'sigmoid')
])


In [163]:
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
print(model.summary())

Model: "sequential_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_5 (Embedding)     (None, 25, 100)           6901400   
                                                                 
 lstm_10 (LSTM)              (None, 25, 64)            42240     
                                                                 
 lstm_11 (LSTM)              (None, 16)                5184      
                                                                 
 dense_5 (Dense)             (None, 1)                 17        
                                                                 
Total params: 6,948,841
Trainable params: 47,441
Non-trainable params: 6,901,400
_________________________________________________________________
None


In [164]:
x=np.array(x_train)
y_tra=np.array(y)

In [165]:
y_tra[:10]

array([1, 1, 1, 0, 1, 1, 1, 0, 0, 1])

In [166]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(x, y_tra, test_size=0.33, random_state=42)

In [167]:
model.fit(X_train,y_train,epochs=5,batch_size=32)

Epoch 1/5
1047/1047 [==============================] - 40s 34ms/step - loss: 0.5680 - accuracy: 0.7025
Epoch 2/5
1047/1047 [==============================] - 35s 33ms/step - loss: 0.4999 - accuracy: 0.7531
Epoch 3/5
1047/1047 [==============================] - 36s 34ms/step - loss: 0.4624 - accuracy: 0.7791
Epoch 4/5
1047/1047 [==============================] - 34s 33ms/step - loss: 0.4354 - accuracy: 0.7952
Epoch 5/5
1047/1047 [==============================] - 36s 34ms/step - loss: 0.4073 - accuracy: 0.8133


In [223]:
y_glove_pred=model.predict(X_test)

516/516 [==============================] - 7s 12ms/step


In [227]:
for i in range(len(y_glove_pred)):
  if(y_glove_pred[i]>0.5):
    y_glove_pred[i]=1;
  else:
    y_glove_pred[i]=0;

In [228]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test,y_glove_pred)

0.7698787878787878

## one hot encoding

In [202]:
from keras.preprocessing.text import one_hot
onehotxtrain=[one_hot(senct,vocab_length) for senct in corpus]

In [203]:
onehot_xtrain=tf.keras.utils.pad_sequences(onehotxtrain,maxlen=25,padding='post')

In [204]:
# from tensorflow.keras.preprocessing.sequence import pad_sequences
# onehot=pad_sequences(onehot_xtrain,padding='post',maxlen=20)

In [205]:
onehot_xtrain[101]

array([61623, 24372, 33917, 38200, 52697, 28340, 65865,  6462, 55447,
       23686, 22086,  8295, 50793,  8295, 44420,   774, 21933, 19189,
       35038, 10353, 36261, 53194, 32169, 47552, 68338], dtype=int32)

In [206]:
x_trainone=np.array(onehot_xtrain)
x_trainone

array([[36766, 50488, 33857, ..., 15655, 25675, 46149],
       [57830, 41884, 29563, ..., 59176, 60010, 39941],
       [ 5001, 11722, 39740, ..., 24372, 49856, 35468],
       ...,
       [ 5623,  4166, 24345, ..., 66967, 33148, 59171],
       [55351, 60682, 60682, ..., 50936, 14642, 60689],
       [30795,  8155, 24112, ...,  3033, 14526, 32198]], dtype=int32)

In [207]:
y_tra

array([1, 1, 1, ..., 0, 0, 0])

In [208]:
from sklearn.model_selection import train_test_split
x_train2, x_test2, y_train2, y_test2 = train_test_split(x_trainone, y_tra, test_size=0.20, random_state=42)

In [209]:
x_train2

array([[66844, 15252, 61462, ..., 12110, 19494, 30370],
       [40495,  3124,  7485, ..., 39033, 46259,  3694],
       [44917, 46408, 31765, ..., 28680, 38450,  8182],
       ...,
       [35620, 15926,  8182, ..., 20042, 20486, 22938],
       [42801,  1036,  4808, ...,  3694, 31568,  5074],
       [69006, 24112, 25898, ..., 52704, 46408, 39365]], dtype=int32)

In [210]:
from sklearn.naive_bayes import MultinomialNB
histroy = MultinomialNB()
histroy.fit(x_train2, y_train2)

MultinomialNB()

In [211]:
y_pred=histroy.predict(x_test2)

In [212]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test2,y_pred)

0.4978

In [217]:
model_hot = Sequential([
    Embedding(input_dim = vocab_length,
              output_dim = embed_size,
              input_length = 25,
             ),
    LSTM(64,return_sequences=True),
    LSTM(16),
    Dense(1, activation = 'sigmoid')
])

In [218]:
model_hot.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
print(model_hot.summary())

Model: "sequential_10"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding_10 (Embedding)    (None, 25, 100)           6901400   
                                                                 
 lstm_20 (LSTM)              (None, 25, 64)            42240     
                                                                 
 lstm_21 (LSTM)              (None, 16)                5184      
                                                                 
 dense_10 (Dense)            (None, 1)                 17        
                                                                 
Total params: 6,948,841
Trainable params: 6,948,841
Non-trainable params: 0
_________________________________________________________________
None


In [219]:
from sklearn.model_selection import train_test_split
X_train3, X_test3, y_train3, y_test3 = train_test_split(x_trainone, y_tra, test_size=0.20, random_state=42)

In [220]:
model_hot.fit(X_train3,y_train3,epochs=5,batch_size=64)

Epoch 1/5
625/625 [==============================] - 86s 132ms/step - loss: 0.4551 - accuracy: 0.7832
Epoch 2/5
625/625 [==============================] - 88s 141ms/step - loss: 0.3165 - accuracy: 0.8647
Epoch 3/5
625/625 [==============================] - 83s 133ms/step - loss: 0.2208 - accuracy: 0.9081
Epoch 4/5
625/625 [==============================] - 83s 133ms/step - loss: 0.1481 - accuracy: 0.9423
Epoch 5/5
625/625 [==============================] - 83s 134ms/step - loss: 0.0963 - accuracy: 0.9640


In [234]:
y_onehot_pred=model_hot.predict(X_test3)

313/313 [==============================] - 4s 10ms/step


In [235]:
for i in range(len(y_onehot_pred)):
  if(y_onehot_pred[i]>0.5):
    y_onehot_pred[i]=1;
  else:
    y_onehot_pred[i]=0;

In [236]:
from sklearn.metrics import accuracy_score
accuracy_score(y_test3,y_onehot_pred)

0.7773

## Bag OF Words

In [ ]:
from sklearn.feature_extraction.text import CountVectorizer
cv=CountVectorizer(binary=True)
x_cv=cv.fit_transform(corpus).toarray()

In [ ]:
from sklearn.model_selection import train_test_split
x_train_bow, x_test_bow, y_train_bow, y_test_bow = train_test_split(x, y, test_size=0.33, random_state=42,stratify=True)

In [ ]:
model_bow = Sequential([
    Embedding(input_dim = vocab_length,
              output_dim = embed_size,
              input_length = 100,
             ),
    LSTM(64,return_sequences=True),
    LSTM(16),
    Dense(1, activation = 'softmax')
])

In [ ]:
model_bow.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
print(model_bow.summary())